In [1]:
from dask.distributed import Client
client = Client()  # Connect to distributed cluster and override default

In [2]:
client

<Client: 'tcp://127.0.0.1:57018' processes=5 threads=20, memory=63.71 GiB>

In [3]:
###################################################################################################################
# Enumerating graphs in R(K4,J5,18) by adding edges between R(K3, J5, 7) and R(K4, J4, 10)
###################################################################################################################
import time
import math
from itertools import permutations
import numpy as np
import pandas as pd
from numba import njit, guvectorize, prange, uint8, uint64, int32, int64, char
import dask.array as da
import dask.dataframe as dd

In [4]:
###################################################################################################################
# Returns convenient strings for printing

def printBit(decimal, n): # Binary form of decimal number
    return bin(int(decimal))[2:].zfill(n)

def printBitList(decimalList, n): # Binary form of tuple of decimal numbers
    return "\n".join(tuple(printBit(decimal, n) for decimal in decimalList))

def printDict(dict): # Key value pairs of a dictionary on seperate lines.
    return "\n".join(str(key) + ": " + str(dict[key]) for key in dict) + "\n"
###################################################################################################################

In [5]:
###################################################################################################################
# Decoding and Formating

def decodeG6(compressed): # Decodes graphs in g6 format to their adjacency matrixes
    n = ord(compressed[0]) - 63 # number of vertices
    length = int(n*(n - 1)/2) # number of 1's and 0's representing upper triangle of adjacency matrix

    bitVect = "" # Our bit vector will be represented by a string
    for character in compressed[1:]:
        bitVect += bin(ord(character) - 63)[2:].zfill(6) # subtract 63 from each byte and string the information together
    bitVect = bitVect[:length] # make sure our bit vector is the correct length

    adjacencyMatrix = [[0 for i in range(n)] for j in range(n)] # Our adjacency matrix will be a list of lists
    index = 0
    for column in range(1, n):
        for row in range(column):
            adjacencyMatrix[row][column] = adjacencyMatrix[column][row] = int(bitVect[index]) ^ 1# We iterate through the rows and the columns, filling them out as we go
            index += 1
    return adjacencyMatrix

def formatBitList(bitVect): # Takes a list bit vector and converts it into an int representing the bit vector
    num = 0
    for i in bitVect[:-1]:
        num = (num + i) << 1
    return num + bitVect[-1]

def formatGraph(adjacencyMatrix):# Takes lists of lists adjacency matrix and converts it into a tuple of ints
    return tuple(formatBitList(row) for row in adjacencyMatrix)
###################################################################################################################

In [6]:
###################################################################################################################
# Finds feasible cones: subsets of the original graph that do not contain triangles and whose complements do not contain independent 3-sets.
# n will always denote the total number of vertices.

def bitIndex(bitVect, i): # Finds ith digit, starting from the right
    return (bitVect & (1 << i)) >> i

def expand(bitSet, n): # Expands a set represented in bits to its individual elements, also represented in bits
    return [1 << i for i in range(n) if bitIndex(bitSet, i)]

def maxClique(R, P, X, maxCliques, adjacencyMatrix, n): # Bron-Kerbosch algoithm for finding maximal cliques: https://en.wikipedia.org/wiki/Bron%E2%80%93Kerbosch_algorithm
    if P == 0 and X == 0:
        maxCliques.append(R)
        return None
    u = n - (P | X).bit_length()
    for v in expand(P & ~adjacencyMatrix[u], n):
        neighbors = adjacencyMatrix[n - v.bit_length()]
        maxClique(R | v, P & neighbors, X & neighbors, maxCliques, adjacencyMatrix, n)
        P = P & ~v
        X = X | v

def complement(adjacencyMatrix, n): # Takes complement of a formatted adjacency matrix
    flip = (1 << n) - 1
    return tuple(flip ^ adjacencyMatrix[row] ^ (1 << (n - row - 1)) for row in range(n))

def maxSet(R, P, X, maxSets, adjacencyMatrix, n): # Finds maximal independent sets
    compMatrix = complement(adjacencyMatrix, n) # Uses complement
    return maxClique(R, P, X, maxSets, compMatrix, n)

def feasibleCones(H, n):
    # Add triangle conditions
    triangles = []
    maxClique(0, (1 << n) - 1, 0, triangles, H, n)
    triangles = [triangle for triangle in triangles if bin(triangle).count('1') == 3] # Looks only at at maximal cliques of three

    ind3sets = []
    maxSet(0, (1 << n) - 1, 0, ind3sets, H, n)
    ind3sets = [set for set in ind3sets if bin(set).count('1') == 3]

    posSolutions = np.arange(1 << n, dtype=np.uint8)
    boolMask = np.full(1 << n, True)

    for triangle in triangles:
        boolMask &= triangle & ~posSolutions != 0

    for ind3set in ind3sets:
        boolMask &= ind3set & posSolutions != 0

    solutions = posSolutions[boolMask]
    return np.reshape(solutions, (len(solutions), 1))
###################################################################################################################

In [7]:
###################################################################################################################
# Repertoire of clique and j subgraph finding functions.

def findSmaller(maximalList, order, n): # Finds cliques of order one less than maximal
    smaller = []
    for maximal in maximalList:
        size = bin(maximal).count('1')
        if size == order - 1:
            smaller.append(maximal) # The subgraph is of correct size.
        elif size == order:
             for i in range(n):
                sub = maximal & ~(1 << i)  # Possible subgraph of maximal clique of correct order
                if bitIndex(maximal, i) == 1 and sub not in smaller: # Ensures there are no duplicates
                    smaller.append(sub)
    return smaller

def findJ(smaller, larger, order): # Finds J graphs, infering from a larger and smaller list of indpendent sets or cliques
    j = []
    length = len(smaller)
    if length > 1: # Ensures there are enough of the smaller subgraphs
        for k in range(length - 1):
            for l in range(k + 1, length): # Iterates through all pairs  of smaller subgraphs
                first, second = smaller[k], smaller[l]
                if bin(first & second).count('1') == order - 2: # Checks the intersection on the set of their vertices is of the correct order
                    combo = first | second
                    if combo not in larger: # Ensures that the union of their sets of vertices is not in the list of larger subgraphs
                        j.append(combo)
    return j

def maximalToMaximum(maximal, order): # Finds the maximum order graphs in a list of maximal subgraphs
    return [sub for sub in maximal if bin(sub).count('1') == order]
###################################################################################################################

In [8]:
###################################################################################################################
# Defines a class for the H graphs, which are in R(K4, J4, 10)
def isContains(bitVect1, bitVect2): # Determines if the set represented by bitVect2 is contained within the set represented by bitVect1
    return (bitVect2 & ~bitVect1) == 0

def H1(G, n, x):
    solution = 0
    pointer = 1 << n
    for row in G:
        pointer >>= 1
        if row & x != 0:
            solution |= pointer
    return solution

def H2(G, n, x):
    solution = 0
    pointer = 1 << n
    for row in G:
        pointer >>= 1
        check = row & x
        while check & (check - 1) != 0:
            length = check.bit_length()
            if G[n - length] & row & x != 0:
                solution |= pointer
                break
            check ^= 1 << (length - 1)
    return solution

def H3(G, n, x):
    solution = 0
    pointer = 1 << n
    for row in G:
        pointer >>= 1
        check = row & x
        while check != 0:
            length = check.bit_length()
            vertex = 1 << (length - 1)
            neighborhood = G[n - length]
            if (x & neighborhood & ~row & ~pointer) != 0 or (x & row & ~neighborhood & ~vertex)!= 0:
                solution |= pointer
                break
            check ^= vertex
    return solution
###################################################################################################################

In [9]:
###################################################################################################################
# Defines a class for the G graphs, storing them in a double tree structure suitable for collapsing the G graphs

def findIndices(bitVector, n): # Turns a bit vector into a list of vertices
    indices = []
    pointer = 1
    for i in range(0, n):
        if bitVector & pointer != 0:
            indices.append(n - i - 1) # Iterates through the bit vector, checking if the value is equal to 1
        pointer <<= 1
    return indices

def excludedJ3(k2, e2, adjacencyMatrix, n): # Finds J3 that consist of the last vertex, a non-neighbor, and a neighbor
    j3 = []
    for neighbor in k2:
        neighborPos = (1 << (n - neighbor - 1))
        neighbors = adjacencyMatrix[neighbor]
        for notNeighbor in e2: # Iterates through all non-neighbors and neighbors
            notNeighborPos = (1 << (n - notNeighbor - 1))
            if neighbors & notNeighborPos == 0: # Ensures that the non-neighbor and the neighbor are unconnected
                j3.append(neighborPos | notNeighborPos | 1) # I
    return j3

def excludedJ4(excludedJ3, e3): # Finds J4 that consist of the last vertex, two non-neighbors, and a neighbor
    j4 = []
    length = len(excludedJ3)
    if length > 1: # Ensures there are enough of the excluded J3, which are subgraphs of excluded J4
        for k in range(length - 1):
            for l in range(k + 1, length): # Iterates through all pairs of the excluded J3
                first, second = excludedJ3[k], excludedJ3[l]
                combo = 1 | (first ^ second)
                if bin(combo).count('1') == 3 and combo in e3: # Ensures that the two excluded J3 form an excluded J4
                    j4.append(first | second)
    return j4

def findSmaller2(maximalList, order, n): # Adjusted findSmaller()
    smaller = []
    for maximal in maximalList:
        size = bin(maximal).count('1')
        if size == order - 1:
            smaller.append(maximal)
        elif size == order:
             for i in range(n):
                sub = maximal & ~(1 << i)
                if bitIndex(maximal, i) == 1 and sub not in smaller and sub & 1 == 1: # Ensures the subgraph included the last vertex
                    smaller.append(sub)
    return smaller
###################################################################################################################

In [10]:
def perms(n): # Finds all permutations of tuples of length n
    return list(permutations(range(n)))

def permuteBit(perm, bitVector, n): # Permutes a bit vector
    permuted = 0
    for i in range(n):
        index = perm[i]
        permuted |= ((1 << (n - index - 1)) & bitVector) >> (n - index - 1) << (n - i - 1) # Locate required bit and add it to our new vector
    return permuted

def permuteMatrix(perm, matrix, n): # Permutes formatted adjacency matrix
    return tuple(permuteBit(perm, matrix[i], n) for i in perm)

In [11]:
###################################################################################################################
def e4(growthCone, cone1, cone2, cone3, flip):
    intersection = (growthCone & cone1) | (growthCone & cone2) | (growthCone & cone3) | (cone1 & cone2) | (cone1 & cone3) | (cone2 & cone3)
    return flip & ~intersection

def j4(growthCone, cone1, cone2, cone3, flip):
    union = growthCone | cone1 | cone2 | cone3
    return flip & ~union

def j3(growthCone, cone1, cone2, h1CompDict):
    union = growthCone | cone1 | cone2
    return h1CompDict[union] & ~union

def e3(growthCone, cone1, cone2, h1CompDict, h1Dict2):
    union = growthCone | cone1 | cone2
    intersection = (growthCone & cone1) | (growthCone & cone2) | (cone1 & cone2)
    return (h1CompDict[union] & ~intersection) | (h1Dict2[union] & ~union)

def e2(growthCone, cone1, h3Dict):
    union = growthCone | cone1
    return h3Dict[union] & ~union

def k2(growthCone, cone1, h1Dict):
    intersection = growthCone & cone1
    return h1Dict[intersection] & intersection
###################################################################################################################

In [12]:
###################################################################################################################
class Node(object):
    nodesDict = {i:[] for i in range(1, 9)} # Keeps track of all nodes
    collapsedDict = {i:[] for i in range(1, 9)}
    mainDict = {i:[] for i in range(1, 9)} # Keeps track of main nodes
    adjunctDict = {1: 1, 2: 1, 3: 2, 4: 2, 5: 3, 6: 3, 7: 4, 8: 4} # Static dictionary, stores the adjunct numbers for graphs of different sizes
    adjunctIndicesDict = {1: 1, 2: 1, 3: int('101', 2), 4: int('1001', 2), 5: int('11001', 2), 6: int('110001', 2), 7: int('1110001', 2), 8: int('11100001', 2)} # Static dictionary, keeps track of the indices of vertices in the adjunct
    permsDict = {i:perms(i) for i in range(1, 9)} # Static dictionary, stores permutatations of tuples of different lengths

    def __init__(self, n, graph, isCollapsed, isMain):
        self.code = False
        self.graph = graph # Formatted adjacency matrix of graph
        self.n = n # Size of graph
        self.isCollapsed = isCollapsed
        self.isMain = isMain
        Node.nodesDict[n].append(self)
        self.id = "level" + str(n) + "ele" + str(len(Node.nodesDict[n]))
        if isMain:
            Node.mainDict[n].append(self)
        
        if n > 1:
            # Creates a parent node
            parentGraph = tuple((row & ~1) >> 1 for row in graph[:-1])
            for node in Node.nodesDict[n - 1]:
                if node.graph == parentGraph:
                    self.parent = node
                    if isMain:
                        if not self.parent.isMain:
                            self.parent.isMain = True
                            Node.mainDict[n - 1].append(self.parent)
                    break
            else:
                self.parent = Node(n - 1, parentGraph, False, isMain)
                
            # Creates an adjunct node
            adjunctNum = Node.adjunctDict[n]
            adjunctGraph = graph[:adjunctNum - 1] + (graph[-1],)
            flipAdjunct = (1 << (n - adjunctNum + 1)) - 1
            adjunctGraph = tuple(((row & ~flipAdjunct) >>  (n - adjunctNum)) | (row & 1) for row in adjunctGraph)
            for node in Node.nodesDict[adjunctNum]:
                if node.graph == adjunctGraph:
                    self.adjunct = node
                    break
            else:
                self.adjunct = Node(adjunctNum, adjunctGraph, False, False)

            # Finds important subgraphs
            flipGraph = (1 << n) - 1
            neighbors = graph[-1]
            k2 = findIndices(neighbors, n)
            notNeighbors = (flipGraph & ~neighbors) ^ 1
            e2 = findIndices(notNeighbors, n)
            notEdges = [1 | notNeighbor for notNeighbor in expand(notNeighbors, n)]

            j3plus = excludedJ3(k2, e2, graph, n)

            maxSets = []
            maxSet(1, notNeighbors, 0, maxSets, graph, n)
            ind4sets = maximalToMaximum(maxSets, 4)
            ind3sets = findSmaller2(maxSets, 4, n)
            j3sets = findJ(notEdges, ind3sets, 3)
            j3sets += j3plus
            j4sets = findJ(ind3sets, ind4sets, 4)
            j4sets += excludedJ4(j3plus, ind3sets)

            # Stores subgraphs as indices of vertices
            self.k2 = np.array([i for i in k2 if i > adjunctNum - 2], dtype=np.uint8)
            self.e2 = np.array([i for i in e2 if i > adjunctNum - 2], dtype=np.uint8)

            adjunctIndices = Node.adjunctIndicesDict[n]
            self.j3 = np.array([findIndices(sub ^ 1, n) for sub in j3sets if not isContains(adjunctIndices, sub)], dtype=np.uint8)
            self.e3 = np.array([findIndices(sub ^ 1, n) for sub in ind3sets if not isContains(adjunctIndices, sub)], dtype=np.uint8)
            self.j4 = np.array([findIndices(sub ^ 1, n) for sub in j4sets if not isContains(adjunctIndices, sub)], dtype=np.uint8)
            self.e4 = np.array([findIndices(sub ^ 1, n) for sub in ind4sets if not isContains(adjunctIndices, sub)], dtype=np.uint8)
    
    def collapse(self, flip, h1Dict, h1Dict2, h1CompDict, h3Dict): 
        parent = self.parent
        adjunct = self.adjunct
        
        if not parent.isCollapsed:
            parent.collapse(flip, h1Dict, h1Dict2, h1CompDict, h3Dict)
        if not adjunct.isCollapsed:
            adjunct.collapse(flip, h1Dict, h1Dict2, h1CompDict, h3Dict)
        
        if not parent.code or not adjunct.code:
            self.isCollapsed = True
            Node.collapsedDict[self.n].append(self)
            return None
        
        if self.n < 5:
            isomorphismList = {permuteMatrix(permutation, self.graph, self.n): {str(i):str(permutation[i]) for i in range(self.n)} for permutation in Node.permsDict[self.n]}
            for node in Node.collapsedDict[self.n]:
                if node.graph in isomorphismList:
                    if node.code:
                        isoNeighborhoods = dd.read_parquet(node.id, engine='pyarrow').rename(columns=isomorphismList[node.graph])[[str(i) for i in range(self.n)]]
                        dd.to_parquet(isoNeighborhoods, self.id, engine='pyarrow', write_index=False, overwrite=True, write_metadata_file=False)  
                        self.code = True
                    self.isCollapsed = True
                    Node.collapsedDict[self.n].append(self)
                    return None
        
        shared = adjunct.n - 1
        parentNeighborhoods = dd.read_parquet(parent.id, engine='pyarrow', index=False)
        adjunctNeighborhoods = dd.read_parquet(adjunct.id, engine='pyarrow', index=False)
        
        if shared == 0:
            posNeighborhoods = dd.merge(parentNeighborhoods.assign(key=1), adjunctNeighborhoods.assign(key=1), on='key').drop(columns='key')
        else:
            posNeighborhoods = dd.merge(parentNeighborhoods, adjunctNeighborhoods, how='inner', on=[str(i) for i in range(shared)])

        posNeighborhoods = posNeighborhoods.to_dask_array(lengths=True)
        
        if posNeighborhoods.shape[0] == 0:
            self.isCollapsed = True
            Node.collapsedDict[self.n].append(self)
            return None
        
        growthCone = posNeighborhoods[:, -1]
        boolNeighborhoods = da.zeros_like(growthCone)
        e4g, j4g, j3g, e3g, e2g, k2g = self.e4, self.j4, self.j3, self.e3, self.e2, self.k2
        
        for i in range(len(e4g)):
            sub = e4g[i]
            boolNeighborhoods |= e4(growthCone, posNeighborhoods[:, sub[0]], posNeighborhoods[:, sub[1]], posNeighborhoods[:, sub[2]], flip)
        
        for i in range(len(j4g)):
            sub = j4g[i]
            boolNeighborhoods |= j4(growthCone, posNeighborhoods[:, sub[0]], posNeighborhoods[:, sub[1]], posNeighborhoods[:, sub[2]], flip)

        for i in range(len(j3g)):
            sub = j3g[i]
            boolNeighborhoods |= j3(growthCone, posNeighborhoods[:, sub[0]], posNeighborhoods[:, sub[1]], h1CompDict)

        for i in range(len(e3g)):
            sub = e3g[i]
            boolNeighborhoods |= e3(growthCone, posNeighborhoods[:, sub[0]], posNeighborhoods[:, sub[1]], h1CompDict, h1Dict2)

        for i in range(len(e2g)):
            boolNeighborhoods |= e2(growthCone, posNeighborhoods[:, e2g[i]], h3Dict)

        for i in range(len(k2g)):
            boolNeighborhoods |= k2(growthCone, posNeighborhoods[:, k2g[i]], h1Dict)
        
        boolMask = boolNeighborhoods == 0
        if boolMask.any().compute():
            posNeighborhoods = posNeighborhoods[boolMask]
            posNeighborhoods = dd.from_dask_array(posNeighborhoods, columns=[str(i) for i in range(self.n)])
            posNeighborhoods = posNeighborhoods.repartition(partition_size='1MB')
            dd.to_parquet(posNeighborhoods, self.id, engine='pyarrow', write_index=False, overwrite=True, write_metadata_file=False)   
            self.code = True
        self.isCollapsed = True
        Node.collapsedDict[self.n].append(self)
        return None
    
###################################################################################################################

In [13]:
def toGraphs(G, gSize, H, hSize, neighborhoods): # Joins two graphs G and H, with knowledge of connections in between them as given by neighborhood
    n = 1 + gSize + hSize
    graphs = np.zeros((neighborhoods.shape[0], n), dtype=np.uint64)
    graphs[:, 1:(gSize + 1)] = (np.asarray(G) << hSize) | neighborhoods
    graphs[:, (gSize + 1):] = np.asarray(H)
    graphs[:, 0] = ((1 << (gSize + 1)) - 1) << hSize
    return graphs

def isk4j6(graph, n): # Checks if successful gluings are in R(K4, J5)
    maxCliques = []
    maxClique(0, (1 << n) - 1, 0, maxCliques, graph, n)
    # for max in maxCliques:
    #     if bin(max).count('1') >= 4: # Ensures there are no cliques of order greater than 3
    #         return False

    maxSets = []
    maxSet(0, (1 << n) - 1, 0, maxSets, graph, n)

    smaller = []
    for max in maxSets:
        vertexCount = bin(max).count('1')
        if vertexCount >= 6: # Ensures there are no independent sets of order greater than 4
            return False

        if vertexCount == 5:
            for small in smaller:
                if bin(max & small).count('1') == 4: # Ensures there are no independent J5's of order 5
                    print(bin(max | small)[2:].zfill(n))
                    return False
            smaller.append(max)
    return True

In [14]:
def compressG6(formatMatrix, n): # Compresses formatted adjacency matrix into g6 format for storage, inverse of decodeG6()
    bitVect = 0
    count = 0
    for i in range(n - 1):
        pointer = 1 << (n - i - 2)
        for j in range(i + 1):
            bitVect <<= 1
            bitVect += (formatMatrix[j] & pointer) >> (n - i - 2)
            count += 1

    size = int(n*(n - 1)/2)
    size6 = size % 6 + size
    bitVect <<= size6 - size
    stringVect = (bin(bitVect)[2:]).zfill(size6)
    code = [int(stringVect[6 * i: 6 * i + 6], 2) + 63 for i in range(int(size6 / 6))]
    return chr(n + 63) + "".join(chr(int(stringVect[6 * i: 6 * i + 6], 2) + 63) for i in range(int(size6 / 6)))

In [17]:
@njit([uint8[:, :](uint64[:, :], int64, int64, int64)])
def jit_compressG6(formatMatrices, n, size, stringLength): # Compresses formatted adjacency matrix into g6 format for storage, inverse of decodeG6()
    outLength = formatMatrices.shape[0]
    full = np.zeros((outLength, size), dtype=np.uint8)
    
    for k in prange(outLength):
        index = 0
        for i in range(n - 1):
            pointer = 1 << (n - i - 2)
            for j in range(i + 1):
                full[k][index] = (pointer & formatMatrices[k][j]) >> (n - i - 2)
                index += 1

    out = np.empty((outLength, stringLength), dtype=np.uint8)
    out[:, 0] = n + 63
    
    multiplier = 2 ** np.arange(5, -1, -1)
    for i in range(stringLength - 1):
        slice6 = full[:, 6*i : 6*i + 6] 
        out[:, i + 1] = np.sum(slice6 * multiplier, axis=1) + 63
    return out.astype(np.uint8)


def compressG6(formatMatrices, n):
    size = n*(n - 1)//2
    size += (6 - size % 6) % 6
    stringLength = size//6 + 1
    
    intArr = jit_compressG6(formatMatrices, n, size, stringLength)
    return np.char.decode(intArr.view('S' + str(stringLength)).ravel())

In [18]:
###################################################################################################################
# Final gluing algorithm for G's and H's
def glueG2H(listG, gSize, listH, hSize, Node): # Glues together a list of G's and H's
    Gs = [Node(gSize, g, False, True) for g in listG]
    index = 0
    count = 0
    
    for h in listH:
        start = time.time()
        startingNeighborhoods = feasibleCones(h, hSize)
        if startingNeighborhoods.shape[0] == 0:
            print("\nCollapse took " + str(time.time() - start))
            continue
            
        index += 1
        print("**" + str(index) + "******************************************************************************************************************")
        flip = (1 << hSize) - 1

        h1Dict = da.from_array(np.array([H1(h, hSize, i) for i in range(flip + 1)], dtype=np.uint8))
        h1Dict2 = da.from_array(np.array([H1(h, hSize, i) for i in range(flip, -1, -1)], dtype=np.uint8))

        compH = complement(h, hSize)
        h1CompDict = da.from_array(np.array([H1(compH, hSize, i) for i in range(flip, -1, -1)], dtype=np.uint8))
        h3Dict = da.from_array(np.array([H3(compH, hSize, i) for i in range(flip, -1, -1)], dtype=np.uint8))

        for root in Node.nodesDict[1]: # Sets the root node for this H
            startingNeighborhoods = dd.from_array(startingNeighborhoods, columns=['0'])
            dd.to_parquet(startingNeighborhoods, 'level1ele1', engine='pyarrow', write_index=False, overwrite=True, write_metadata_file=False) 
            root.isCollapsed = True
            root.code = True
            Node.collapsedDict[1].append(root)
        
        for i in range(2, gSize + 1): # Collapses nodes
            for node in Node.mainDict[i]:
                node.collapse(flip, h1Dict, h1Dict2, h1CompDict, h3Dict)
        
        neighborhoods = [toGraphs(g.graph, gSize, h, hSize, dd.read_parquet(g.id, engine='pyarrow', index=False).values.compute()) for g in Gs if g.code]
        if len(neighborhoods) == 1:   
            neighborhoods = neighborhoods[0]
        elif len(neighborhoods)!= 0:
            neighborhoods = np.concatenate(neighborhoods)
        
        if len(neighborhoods) != 0:
            count += neighborhoods.shape[0]
            glueH = open('hGluings/h' + str(index) + 'gluings.txt', 'w')
            np.savetxt('hGluings/h' + str(index) + 'gluings.txt', compressG6(neighborhoods, gSize + hSize + 1), fmt='%s')
            glueH.close()

        Node.collapsedDict = {i:[] for i in range(1, 9)}
        for i in range(1, gSize + 1): # Resets the nodes for the next H
            for node in Node.nodesDict[i]:
                node.isCollapsed = False
                node.code = False
    
        print("\nCollapse took " + str(time.time() - start))

    return count

###################################################################################################################

In [ ]:
# run #############################################################################################################
with open('dataset_k4kme/k4k4e_08.g6', 'r') as file:
    k4j4 = file.read().splitlines()
k4j4 = [formatGraph(decodeG6(graph)) for graph in k4j4] # Relevant H's

with open('dataset_k3kme/k3k5e_08.g6', 'r') as file:
    orig = file.read().splitlines()
k3j5 = [formatGraph(decodeG6(graph)) for graph in orig]  # Relevant G's

start = time.time()
n = 8
gluings = glueG2H(k3j5, n, k4j4, n, Node) # Glues G's to H's
print("Total gluings: " + str(gluings))
print("Total time: ", time.time() - start)